In [ ]:
!pip install -q langgraph langchain-huggingface langchain-google-genai langchain-community tiktoken gradio faiss-cpu pypdf pydantic requests==2.32.4 google-ai-generativelanguage==0.6.15 google-genai duckduckgo-search faster-whisper sounddevice

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.7/43.7 kB 3.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 153.3/153.3 kB 7.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.0/42.0 kB 2.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.5/2.5 MB 79.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 31.4/31.4 MB 42.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 322.5/322.5 kB 10.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 40.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 39.9/39.9 MB 16.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 38.8/38.8 MB 10.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.9/43.9 kB 2.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.8/56.8 kB 3.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.3/17.3 MB 30.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.3/3.3 MB 

In [ ]:
import os
from google.colab import userdata
GEMINI_API_KEY=userdata.get('GOOGLE_API_KEY')

os.environ["GOOGLE_API_KEY"] = GEMINI_API_KEY

In [ ]:
import langchain
import langchain_community
import gradio
import tiktoken
import faiss
from langchain_google_genai import ChatGoogleGenerativeAI
from langchain_huggingface import HuggingFaceEmbeddings, HuggingFacePipeline
from langchain.embeddings import HuggingFaceBgeEmbeddings
from langchain_community.vectorstores import FAISS
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain_core.prompts import PromptTemplate
from langchain.document_loaders import TextLoader
from langchain_community.cross_encoders import HuggingFaceCrossEncoder
from langchain_core.runnables import RunnablePassthrough, RunnableLambda, RunnableParallel
from langchain_community.document_loaders import PyPDFLoader
from langchain_community.document_loaders import PyPDFDirectoryLoader
from langchain.retrievers import ContextualCompressionRetriever
from langchain.retrievers.document_compressors import CrossEncoderReranker
from langchain.output_parsers import PydanticOutputParser
from langchain_core.output_parsers import JsonOutputParser
from langchain.output_parsers import OutputFixingParser
from pydantic import BaseModel, Field
from langgraph.graph import StateGraph, START, END
from typing import TypedDict, Annotated, Literal
from langchain_core.messages import BaseMessage, HumanMessage, AIMessage
from langgraph.graph.message import add_messages
from langgraph.checkpoint.memory import InMemorySaver
from langchain_core.prompts import ChatPromptTemplate
from langchain_core.tools.retriever import create_retriever_tool
from langgraph.prebuilt import ToolNode, tools_condition
from langchain_community.tools import DuckDuckGoSearchRun

import contextlib
import wave
from IPython.display import Audio

from google import genai
from google.genai import types

from faster_whisper import WhisperModel
import sounddevice as sd
import numpy as np


OSError: PortAudio library not found

In [ ]:
model = WhisperModel("small", device="cuda")

# Audio parameters
SAMPLE_RATE = 16000
BLOCK_SIZE = 5  # seconds per chunk

def callback(indata, frames, time, status):
    if status:
        print(status)
    audio = indata[:, 0]  # take first channel
    # Convert to float32 PCM
    audio = (audio * 32767).astype(np.int16).tobytes()

    # Transcribe this chunk
    segments, _ = model.transcribe(audio, beam_size=5)
    for segment in segments:
        print(segment.text, end=" ", flush=True)

# Start recording & transcribing
with sd.InputStream(samplerate=SAMPLE_RATE, channels=1, callback=callback, blocksize=int(SAMPLE_RATE * BLOCK_SIZE)):
    print("🎤 Listening... press Ctrl+C to stop")
    while True:
        pass

NameError: name 'sd' is not defined

In [ ]:
class ChatState(TypedDict):

    messages: Annotated[list[BaseMessage], add_messages]

In [ ]:
def pretty_print_docs(docs):
    print(
        f"\n{'-' * 100}\n".join(
            [f"Document {i + 1}:\n\n" + d.page_content for i, d in enumerate(docs)]
        )
    )


def format_context(context):
  return "\n\n".join([doc.page_content for doc in context])



file_index = 0

@contextlib.contextmanager
def wave_file(filename, channels=1, rate=24000, sample_width=2):
    with wave.open(filename, "wb") as wf:
        wf.setnchannels(channels)
        wf.setsampwidth(sample_width)
        wf.setframerate(rate)
        yield wf

def play_audio_blob(blob):
  global file_index
  file_index += 1

  fname = f'audio_{file_index}.wav'
  with wave_file(fname) as wav:
    wav.writeframes(blob.data)

  return Audio(fname, autoplay=True)

def play_audio(response):
    return play_audio_blob(response.candidates[0].content.parts[0].inline_data)

In [ ]:
file_path = "/content/the-illusion-of-thinking.pdf"

In [ ]:
model_name = "BAAI/bge-small-en-v1.5"
model_kwargs = {'device': 'cuda'}
encode_kwargs = {'normalize_embeddings': True}

model = HuggingFaceEmbeddings(
    model_name=model_name,
    model_kwargs=model_kwargs,
    encode_kwargs=encode_kwargs,
)

modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

README.md: 0.00B [00:00, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/52.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/743 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/366 [00:00<?, ?B/s]

vocab.txt: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [ ]:
model_name = "BAAI/bge-reranker-base"

reranker = HuggingFaceCrossEncoder(
    model_name=model_name,
    model_kwargs = {'device': 'cuda'}
)

config.json:   0%|          | 0.00/799 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/1.11G [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/443 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/17.1M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/279 [00:00<?, ?B/s]

README.md: 0.00B [00:00, ?B/s]

In [ ]:
loader = PyPDFLoader(file_path)
data = loader.load()

splitter = RecursiveCharacterTextSplitter(
            chunk_size=1000,
            chunk_overlap=200,
        )
chunks = splitter.split_documents(data)

vector_store = FAISS.from_documents(chunks, model)

base_retriever = vector_store.as_retriever(
            search_type="mmr",
            search_kwargs={"k": 10, "lambda_mult": 0.5}
        )

compressor = CrossEncoderReranker(model=reranker, top_n=3)
compression_retriever = ContextualCompressionRetriever(
            base_compressor=compressor,
            base_retriever=base_retriever
        )
retriever_tool = create_retriever_tool(
    compression_retriever,
    "retriever",
    "Search and retrievs relevant information about the query asked by user"
)
search_tool = DuckDuckGoSearchRun()

tools = [retriever_tool, search_tool]
tool_node = ToolNode(tools)

In [ ]:
class Answer(BaseModel):
    answer: str = Field(description="answer to the question based on context")

llm_with_tools = ChatGoogleGenerativeAI(model="gemini-2.5-flash").bind_tools(tools)

In [ ]:
def call_model(state: ChatState):
    messages = state['messages']
    response = llm_with_tools.invoke(messages)
    return {"messages": [response]}  # Returns as a list to add to the state

In [ ]:
from langgraph.graph import END, START, StateGraph

workflow = StateGraph(ChatState)


In [ ]:
# Add single node that does both retrieval and answering
workflow.add_node("agent", call_model)
workflow.add_node("tools", tool_node)

# Add edges
workflow.add_edge(START, "agent")
workflow.add_conditional_edges("agent",tools_condition)
workflow.add_edge('tools', 'agent')

checkpointer = InMemorySaver()

app = workflow.compile(checkpointer=checkpointer)

In [ ]:
final_state = app.invoke(
    {"messages": [HumanMessage(content="hi,my name is vatsal. can you Explain me what is discussed in this paper the illusion of thinking")]},
    config={"configurable": {"thread_id": 42}}
)

In [ ]:
(final_state["messages"])

[HumanMessage(content='hi,my name is vatsal. can you Explain me what is discussed in this paper the illusion of thinking', additional_kwargs={}, response_metadata={}, id='91a56096-9adc-4907-9498-c1ee542977d9'),
 AIMessage(content='', additional_kwargs={'function_call': {'name': 'retriever', 'arguments': '{"query": "the illusion of thinking paper"}'}}, response_metadata={'prompt_feedback': {'block_reason': 0, 'safety_ratings': []}, 'finish_reason': 'STOP', 'safety_ratings': []}, id='run--e2654172-ca30-4a2b-a9a1-a513056ca253-0', tool_calls=[{'name': 'retriever', 'args': {'query': 'the illusion of thinking paper'}, 'id': 'b97a900d-9303-4e39-938c-b25d161cc776', 'type': 'tool_call'}], usage_metadata={'input_tokens': 137, 'output_tokens': 18, 'total_tokens': 190, 'input_token_details': {'cache_read': 0}}),
 ToolMessage(content='The Illusion of Thinking:\nUnderstanding the Strengths and Limitations of Reasoning Models\nvia the Lens of Problem Complexity\nParshin Shojaee∗† Iman Mirzadeh∗ Keiva

In [ ]:
client = genai.Client(api_key=GEMINI_API_KEY)
MODEL_ID = "gemini-2.5-flash-preview-tts"

while True:

  query = input("Human: ")
  if query.lower() == "exit":
    break;
  result = app.invoke({"messages":[HumanMessage(content = query)]}, config = {"configurable": {"thread_id": 4}})
  print(f"AI: {result["messages"][-1].content}")

  response = client.models.generate_content(
    model=MODEL_ID,
    contents='""" Say " ' + result["messages"][-1].content + '" """ ',
    config={"response_modalities": ['Audio']},
  )
  blob = response.candidates[0].content.parts[0].inline_data
  play_audio_blob(blob)


Human: can you Explain me what is discussed in this paper the illusion of thinking
AI: The paper "The Illusion of Thinking: Understanding the Strengths and Limitations of Reasoning Models via the Lens of Problem Complexity" investigates Large Reasoning Models (LRMs) and their "thinking processes" (detailed steps generated before providing an answer).

Here's a breakdown of what's discussed:

*   **Focus beyond final answers:** Unlike typical evaluations that focus on accuracy in math and coding benchmarks, this paper delves into the structure and quality of the reasoning traces themselves. This helps overcome issues like data contamination and offers deeper insights into how LRMs work.
*   **Emergent behaviors and limitations:** The paper highlights observed behaviors in LRMs, such as discrepancies between their thought processes and final answers, and the "overthinking phenomenon." Overthinking refers to models generating verbose and redundant outputs even after finding a solution, le

In [ ]:
play_audio_blob(blob)

In [ ]:
result

{'messages': [HumanMessage(content='hi my name is vatsal', additional_kwargs={}, response_metadata={}, id='1c3e7a6c-5c35-49f7-a833-abc17ec73b85'),
  AIMessage(content="Hi Vatsal, it's nice to meet you! How can I help you today?", additional_kwargs={}, response_metadata={'prompt_feedback': {'block_reason': 0, 'safety_ratings': []}, 'finish_reason': 'STOP', 'safety_ratings': []}, id='run--e55cd5e1-071a-492f-86ea-a5dd3337b06a-0', usage_metadata={'input_tokens': 56, 'output_tokens': 20, 'total_tokens': 106, 'input_token_details': {'cache_read': 0}}),
  HumanMessage(content='can you tell what is my name?', additional_kwargs={}, response_metadata={}, id='5f232b4a-fb87-4b1e-ac5c-779c60ee87a9'),
  AIMessage(content='Your name is Vatsal.', additional_kwargs={}, response_metadata={'prompt_feedback': {'block_reason': 0, 'safety_ratings': []}, 'finish_reason': 'STOP', 'safety_ratings': []}, id='run--98df3b0e-b26e-4259-9541-76e2db69b20d-0', usage_metadata={'input_tokens': 86, 'output_tokens': 7, 't